____
__Universidad de San Andrés__<br/>
__Machine Learning__<br/>
__Detección de ballenas__<br/>
__Martin Bianchi y Federico Gutman__
____

nota: haria dos notebooks, uno para el primer dataset y otro para el segundo

### Importamos las librerías necesarias

In [9]:
import numpy as np
import matplotlib.pyplot as plt
import os
import pandas as pd
import librosa
import librosa.display
import seaborn as sns
from tqdm import tqdm

### Cargamos los datos y los visualizamos 

In [12]:
train_dir = r'C:\Users\bianc\Machine\TPFINAL\data\whale-detection-challenge\data\train'

train_files = [f for f in os.listdir(train_dir) if f.endswith('.aiff')]

test_dir = r'C:\Users\bianc\Machine\TPFINAL\data\whale-detection-challenge\data\test'

test_files = [f for f in os.listdir(test_dir) if f.endswith('.aiff')]


Tras cargar los datos de audio, es necesario transformarlos en representaciones numéricas para que los modelos de inteligencia artificial puedan trabajar con ellos. Esto implica procesar las señales acústicas y extraer características significativas. A continuación, describimos los métodos principales que pueden utilizarse:

- **`MFCC (Mel-Frequency Cepstral Coefficients)`**:  
  Este método comienza calculando un `espectrograma` (aplicando la Transformada de Fourier de corto plazo - STFT), que divide la señal en distintas frecuencias a lo largo del tiempo. Luego, estas frecuencias se proyectan en una `escala Mel`, que imita cómo el oído humano percibe el sonido.  
  A partir de esta representación, se aplica un logaritmo a las intensidades (para mejorar la dinámica) y, finalmente, una Transformada Discreta del Coseno (DCT) para condensar la información en coeficientes que capturan la forma general del espectro.  
  ➡️ Ventaja: Representación compacta y eficiente. Ideal para modelos clásicos.  
  ➡️ Desventaja: Pierde algunos detalles espectrales finos.  

- **`Mel Spectrograma`**:  
  Similar al proceso anterior, comienza calculando el `espectrograma` de la señal de audio. Sin embargo, en lugar de condensarlo con una DCT, se mantiene el espectro proyectado en la `escala Mel`. Esto da como resultado una representación en forma de imagen tiempo × frecuencia, donde las intensidades se logarítmizan para reflejar cómo el oído humano percibe las variaciones de energía.  
  ➡️ Ventaja: Más detallado que los MFCC y adecuado para redes neuronales profundas (especialmente CNNs).  
  ➡️ Desventaja: Mayor tamaño y costo computacional que los MFCC.  

- **`Espectrograma (STFT)`**:  
  Esta representación se obtiene directamente de la Transformada de Fourier de corto plazo. Representa cómo varían las frecuencias de la señal en el tiempo, en una escala lineal (sin ajuste perceptual). Es la forma más detallada de analizar la información de frecuencia, pero también contiene mucha redundancia y es la menos comprimida.  
  ➡️ Ventaja: Máxima flexibilidad y detalle. Ideal para análisis detallados o experimentos con modelos avanzados.  
  ➡️ Desventaja: Alto costo computacional y puede incluir información innecesaria para modelos de aprendizaje automático.  

Estos métodos transforman los datos en un formato más estructurado, donde se resaltan patrones acústicos relevantes. La elección de cuál usar dependerá del modelo seleccionado y del equilibrio entre precisión y eficiencia que busquemos en nuestro pipeline.  
En el próximo paso, implementaremos uno de estos enfoques para preparar nuestros datos y avanzar hacia la fase de modelado.

In [21]:
def process_mfcc(files, input_dir, output_dir, n_mfcc=13, sr=22050):
    """
    Calcula los MFCCs de una lista de archivos de audio y guarda los resultados como archivos .npy.
    """
    os.makedirs(output_dir, exist_ok=True)
    for file in files:
        file_path = os.path.join(input_dir, file)
        y, sr = librosa.load(file_path, sr=sr)
        mfccs = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=n_mfcc)
        np.save(os.path.join(output_dir, f"{os.path.splitext(file)[0]}_mfcc.npy"), mfccs)
    print(f"MFCCs guardados en {output_dir}")

def process_mel_spectrogram(files, input_dir, output_dir, sr=22050, n_fft=2048, hop_length=512, n_mels=128):
    """
    Calcula los Mel Spectrogramas de una lista de archivos de audio y guarda los resultados como archivos .npy.
    """
    os.makedirs(output_dir, exist_ok=True)
    for file in files:
        file_path = os.path.join(input_dir, file)
        y, sr = librosa.load(file_path, sr=sr)
        mel_spec = librosa.feature.melspectrogram(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length, n_mels=n_mels)
        mel_spec_db = librosa.power_to_db(mel_spec, ref=np.max)
        np.save(os.path.join(output_dir, f"{os.path.splitext(file)[0]}_mel.npy"), mel_spec_db)
    print(f"Mel Spectrogramas guardados en {output_dir}")

def process_stft(files, input_dir, output_dir, sr=22050, n_fft=2048, hop_length=512):
    """
    Calcula los Espectrogramas (STFT) de una lista de archivos de audio y guarda los resultados como archivos .npy.
    """
    os.makedirs(output_dir, exist_ok=True)
    for file in files:
        file_path = os.path.join(input_dir, file)
        y, sr = librosa.load(file_path, sr=sr)
        stft = np.abs(librosa.stft(y, n_fft=n_fft, hop_length=hop_length))
        stft_db = librosa.amplitude_to_db(stft, ref=np.max)
        np.save(os.path.join(output_dir, f"{os.path.splitext(file)[0]}_stft.npy"), stft_db)
    print(f"Espectrogramas (STFT) guardados en {output_dir}")


In [29]:
output_dir_mfcc = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mfcc_test'
output_dir_mel = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mel_test'
output_dir_stft = r'C:\Users\bianc\Machine\TPFINAL\data_processed\stft_test'

# Procesar con las listas ya 6
# process_mfcc(test_files, test_dir, output_dir_mfcc)
# process_mel_spectrogram(test_files, test_dir, output_dir_mel)
# process_stft(test_files, test_dir, output_dir_stft)

output_dir_mfcc = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mfcc_train'
output_dir_mel = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mel_train'
output_dir_stft = r'C:\Users\bianc\Machine\TPFINAL\data_processed\stft_train'

# Procesar con las listas ya creadas
# process_mfcc(train_files, train_dir, output_dir_mfcc)
# process_mel_spectrogram(train_files, train_dir, output_dir_mel)
# process_stft(train_files, train_dir, output_dir_stft)

In [ ]:
def save_labels_to_csv(features_dir, csv_path, output_csv):
    """
    Asocia los archivos de características con sus etiquetas y guarda el resultado en un archivo CSV.
    """
    # Leer los labels del archivo CSV
    labels_df = pd.read_csv(csv_path)
    labels_dict = dict(zip(labels_df['clip_name'], labels_df['label']))  # filename -> label

    # Crear una lista para guardar los datos asociados
    data = []

    # Asociar cada archivo de características con su label
    for file in os.listdir(features_dir):
        if file.endswith('.npy'):
            filename = file.split('_')[0] + '.aiff'  # Reconstruir el nombre original del archivo
            label = labels_dict.get(filename, None)
            if label is not None:
                data.append({'feature_file': file, 'label': label})
            else:
                print(f"Advertencia: No se encontró un label para {filename}")

    # Guardar los datos asociados en un nuevo archivo CSV
    data_df = pd.DataFrame(data)
    data_df.to_csv(output_csv, index=False)
    print(f"Archivo CSV con etiquetas guardado en {output_csv}")

# Directorios y archivo CSV
train_csv = r'C:\Users\bianc\Machine\TPFINAL\data\whale-detection-challenge\data\train.csv'
output_csv_mfcc = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mfcc_train_labels.csv'
output_csv_mel = r'C:\Users\bianc\Machine\TPFINAL\data_processed\mel_train_labels.csv'
output_csv_stft = r'C:\Users\bianc\Machine\TPFINAL\data_processed\stft_train_labels.csv'

# Asociar labels con los outputs existentes
save_labels_to_csv(output_dir_mfcc, train_csv, output_csv_mfcc)
save_labels_to_csv(output_dir_mel, train_csv, output_csv_mel)
save_labels_to_csv(output_dir_stft, train_csv, output_csv_stft)


Advertencia: No se encontró un label para train10000.aif
Advertencia: No se encontró un label para train10001.aif
Advertencia: No se encontró un label para train10002.aif
Advertencia: No se encontró un label para train10003.aif
Advertencia: No se encontró un label para train10004.aif
Advertencia: No se encontró un label para train10005.aif
Advertencia: No se encontró un label para train10006.aif
Advertencia: No se encontró un label para train10007.aif
Advertencia: No se encontró un label para train10008.aif
Advertencia: No se encontró un label para train10009.aif
Advertencia: No se encontró un label para train1000.aif
Advertencia: No se encontró un label para train10010.aif
Advertencia: No se encontró un label para train10011.aif
Advertencia: No se encontró un label para train10012.aif
Advertencia: No se encontró un label para train10013.aif
Advertencia: No se encontró un label para train10014.aif
Advertencia: No se encontró un label para train10015.aif
Advertencia: No se encontró un l